# How to develop a MEC application using the MEC Sandbox HTTP REST API
This tutorial introduces the step by step procedure to create a basic MEC appcation following ETSI MEC standards.
It uses the ETSI MEC Sandbox simulator.



## What is a MEC application

See [The Wiki MEC web site](https://www.etsi.org/technologies/multi-access-edge-computing)


## The basics of developing a MEC application

The developement of a MEC application follows a strict process in order to access the ETSI MEC services and provides valuable services to the customers.
Mainly, this process can be split in several steps:
1. Global initializations (constant, variables...)
2. Create a new instance of a MEC Sandbox (Note that using an existing one could be a solution too (see Annex A)
3. Activate a network scenario in order to access the ETSI MEC services
4. Create a new application identifier
5. Register our MEC application and subscribe to service termination (see MEC 011)
6. Use MEC services in order to provide valuable services to the customers
    6.1. Apply MEC services required subscriptions (e.g. MEC 013 location subscription)
7. Terminate the MEC application
    7.1. Remove MEC services subscriptions
    7.2. Deactivate the current network scenario
    7.3. Delete the instance of the MEC Sandbox
8. Release all the MEC application resources

## Use the MEC Sandbox HTTP REST API models and code

The MEC sandbox provides a piece of code (the python sub) that shall be used to develop the MEC application and interact with the MEC Sandbox. This piece of code mainly contains swagger models to serialize/deserialize JSON data structures and HTTP REST API call functions.
The openApi file is availabe [here](https://forge.etsi.org/rep/mec/AdvantEDGE/-/blob/Task2_PoC/go-apps/meep-sandbox-sandbox_api/sandbox_api/swagger.yaml) and the [Swagger editor](https://editor-next.swagger.io/) is used to generate the python sub.

The project architecture is describe [here](images/project_arch.jpg).

The sandbox_api folder contains the python implementation of the HTTP REST API definitions introduced by the openApi [file](https://forge.etsi.org/rep/mec/AdvantEDGE/-/blob/Task2_PoC/go-apps/meep-sandbox-sandbox_api/sandbox_api/swagger.yaml).
The model folder contains the python implementation of the data type definitions introduced by the openApi [file](https://forge.etsi.org/rep/mec/AdvantEDGE/-/blob/Task2_PoC/go-apps/meep-sandbox-sandbox_api/sandbox_api/swagger.yaml).
directory:

Before going to create our MEC application skeleton, the following steps shall be done:
1) Change the working directory (see the project architecture)

In [ ]:
import os
os.chdir(os.path.join(os.getcwd(), '../mecapp'))
print(os.getcwd())

2) Apply the python imports

In [ ]:
from __future__ import division # Import floating-point division (1/4=0.25) instead of Euclidian division (1/4=0)

import os
import sys
import re
import logging
import time
import json
import uuid

import pprint

import six

import swagger_client
from swagger_client.rest import ApiException

from http import HTTPStatus
from http.server import BaseHTTPRequestHandler, HTTPServer


3) Initialize of the global constants (cell 3)

In [ ]:
MEC_SANDBOX_URL     = 'https://mec-platform2.etsi.org'                        # MEC Sandbox host/base URL
MEC_SANDBOX_API_URL = 'https://mec-platform2.etsi.org/sandbox-api/v1'         # MEC Sandbox API host/base URL
PROVIDER            = 'Jupyter2024'                                               # Login provider value - To skip authorization: 'github'
MEC_PLTF            = 'mep1'                                                 # MEC plateform name. Linked to the network scenario
LOGGER_FORMAT       = '%(asctime)s - %(name)s - %(levelname)s - %(message)s' # Logging format
STABLE_TIME_OUT     = 6                                                      # Timer to wait for MEC Sndbox reaches its stable state (K8S pods in running state)
LOGIN_TIMEOUT       = 3 #30                                                     # Timer to wait for user to authorize from GITHUB
LISTENER_IP         = '0.0.0.0'                                              # Listener IPv4 address for notification callback calls
LISTENER_PORT       = 32100                                                  # Listener IPv4 port for notification callback calls
CALLBACK_URI        = "https://yanngarcia.ddns.net/jupyter/sandbox/demo6/v1/"

4) Setup the logger instance and the HTTP REST API (cell 4)

In [ ]:
# Initialize the logger
logger = logging.getLogger(__name__)
logger.setLevel(logging.DEBUG)
logging.basicConfig(filename='/tmp/' + time.strftime('%Y%m%d-%H%M%S') + '.log')
l = logging.StreamHandler()
l.setFormatter(logging.Formatter('%(asctime)s - %(name)s - %(levelname)s - %(message)s'))
logger.addHandler(l)

# Setup the HTTP REST API configuration to be used to send request to MEC Sandbox API 
configuration               = swagger_client.Configuration()
configuration.host          = MEC_SANDBOX_API_URL
configuration.verify_ssl    = False
configuration.debug         = True
configuration.logger_format = LOGGER_FORMAT
# Create an instance of ApiClient
sandbox_api = swagger_client.ApiClient(configuration, 'Content-Type', 'application/json')

# Setup the HTTP REST API configuration to be used to send request to MEC Services
configuration1               = swagger_client.Configuration()
configuration1.host          = MEC_SANDBOX_URL
configuration1.verify_ssl    = True
configuration1.debug         = True
configuration1.logger_format = LOGGER_FORMAT
# Create an instance of ApiClient
service_api = swagger_client.ApiClient(configuration1, 'Content-Type', 'application/json')


5) Setup the global variables (cell 5)

In [ ]:
# Initialize the global variables
nw_scenarios    = []   # The list of available network scenarios
nw_scenario_idx = -1   # The network scenario idx to activate (deactivate)
app_inst_id     = None # The requested application instance identifier

## Create our first MEC application

The first step to develop a MEC application is to create the application skeleton which contains the minimum steps below:
 
- Login to instanciate a MEC Sandbox
- Logout to delete a existing MEC Sandbox

### First steps: the login/logout

Here is the first squeleton with the following sequence:
- Login
- Print sandbox identifier
- Logout
- Check that logout is effective


#### The login function

To log to the MEC Sandbox, 
the login process is done in two step. In step 1, a user code is requested to GITHUB. In step 2, the user has to enter this user code to https://github.com/login/device and proceed to the authorization.
Please, pay attention to the log '=======================> DO AUTHORIZATION WITH CODE :' which indicates you the user code to use for the authorization.

It uses the HTTP POST request with the URL 'POST /sandbox-sandbox_api/v1/login?provide=github' (see PROVIDER constant).


In [ ]:
# Login
def process_login() -> str:
    """
    Authenticate and create a new MEC Sandbox instance.

    :return: The sandbox instance identifier on success, None otherwise
    """ 

    global PROVIDER, logger

    logger.debug('>>> process_login')

    try:
        auth = swagger_client.AuthorizationApi(sandbox_api)
        oauth = auth.login(PROVIDER, async_req = False)
        logger.debug('process_login (step1): oauth: ' + str(oauth))
        # Wait for the MEC Sandbox is running
        logger.debug('=======================> DO AUTHORIZATION WITH CODE : ' + oauth.user_code)
        time.sleep(LOGIN_TIMEOUT) # Wait for Authirization from user side
        namespace = auth.get_namespace(oauth.user_code)
        logger.debug('process_login (step2): result: ' + str(namespace))
        return namespace.sandbox_name
    except ApiException as e:
        logger.error('Exception when calling AuthorizationApi->login: %s\n' % e)

    return None
    # End of function process_login


#### The logout function

It uses the HTTP POST request with the URL 'POST /sandbox-sandbox_api/v1/logout?sandbox_name={sandbox_name}'.


In [ ]:
# Logout
def process_logout(sandbox: str) -> int:
    """
    Delete the specified MEC Sandbox instance.

    :param sandbox: The MEC Sandbox to delete
    :return: 0 on success, -1 otherwise
    """

    global logger

    logger.debug('>>> process_logout: sandbox=' + sandbox)

    try:
        auth = swagger_client.AuthorizationApi(sandbox_api)
        result = auth.logout(sandbox, async_req = False)  # noqa: E501
        return 0
    except ApiException as e:
        logger.error('Exception when calling AuthorizationApi->logout: %s\n' % e)
    return -1
    # End of function process_logout


Now, let put in action our Login/Logout functions:

In [ ]:
def process_main():
    """
    This is the skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Logout
        - Check that logout is effective
    This skeleton will be the bas of the next sprint in order to achieve a full implementation of a MEC application
    """ 

    global logger

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        return

    # Print sandbox identifier
    logger.info('Sandbox created: ' + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug('To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A)')
  
    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Second step: Retrieve the list of network scenarios

Let's go futhur and see how we can retrieve the list of the network scenarios available in order to activate one of them and access the MEC services exposed such as MEC 013 or MEC 030.

The sequence will be:
- Login
- Print sandbox identifier
- Print available network scenarios
- Logout
- Check that logout is effective

The login and logout functions are described in cell 3 and 4.

To retrieve the list of the network scenarios, let's create a new function called 'get_network_scenarios'. It uses the HTTP GET request with the URL '/sandbox-sandbox_api/v1/sandboxNetworkScenarios?sandbox_name={sandbox_name}'.

In [ ]:
def get_network_scenarios(sandbox: str) -> list:
    """
    Retrieve the list of the available network scenarios.

    :param sandbox: The MEC Sandbox instance to use
    :return: The list of the available network scenarios on success, None otherwise
    """

    global PROVIDER, logger, configuration

    logger.debug('>>> get_network_scenarios: sandbox=' + sandbox)

    try:
        nw = swagger_client.SandboxNetworkScenariosApi(sandbox_api)
        result = nw.sandbox_network_scenarios_get(sandbox, async_req = False)  # noqa: E501
        logger.debug('get_network_scenarios: result: ' + str(result))
        return result
    except ApiException as e:
        logger.error('Exception when calling SandboxNetworkScenariosApi->sandbox_network_scenarios_get: %s\n' % e)

    return None
    # End of function get_network_scenarios


Putting everything together:

In [ ]:
def process_main():
    """
    This is the first sprint of our skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Logout
        - Check that logout is effective
    """ 
    global logger, nw_scenarios 

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error('Failed to instanciate a MEC Sandbox')
        return

    # Print sandbox identifier
    logger.info('Sandbox created: ' + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error('Failed to retrieve the list of network scenarios')
    elif len(nw_scenarios) != 0:
        logger.info('nw_scenarios: %s', str(type(nw_scenarios[0])))
        logger.info('nw_scenarios: %s', str(nw_scenarios))
    else:
        logger.info('nw_scenarios: No scenario available')

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug('To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A)')
  
    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Third step: Activate and deactivate a network scenario

Having a list of network scenarion, the next step is to actvate (and deactivate) a network scenario. This step is mandatory to create a new application instance id and access the MEC services.

In this section, we will arbitrary activate the network scenario called '4g-5g-macro-v2x', which is at the index 0 of the nw_scenarios. 

In [ ]:
def select_network_scenario_based_on_criteria(criterias_list: list) -> int:
    """
    Select the network scenario to activate based of the provided list of criterias.

    :param criterias_list: The list of criterias to select the correct network scenario
    :return: 0 on success, -1 otherwise
    """
    return 0 # The index of the '4g-5g-macro-v2x' network scenario - Hard coded

#### The activate function

The process to activate a scenario is based on an HTTP POST request with the URL '/sandboxNetworkScenarios/{sandbox_name}?network_scenario_id={network_scenario_id}'.


In [ ]:
def activate_network_scenario(sandbox: str) -> int:
    """
    Activate the specified network scenario.

    :param sandbox: The MEC Sandbox instance to use
    :return: 0 on success, -1 otherwise
    """

    global logger, configuration, nw_scenarios, nw_scenario_idx

    logger.debug('>>> activate_network_scenario: ' + sandbox)

    nw_scenario_idx = select_network_scenario_based_on_criteria([])
    if nw_scenario_idx == -1:
        logger.error('activate_network_scenario: Failed to select a network scenarion')
        return -1

    try:
        nw = swagger_client.SandboxNetworkScenariosApi(sandbox_api)
        result = nw.sandbox_network_scenario_post(sandbox, nw_scenarios[nw_scenario_idx].id, async_req = False)  # noqa: E501
        logger.debug('activate_network_scenario: result: ' + str(result))
        return result
    except ApiException as e:
        logger.error('Exception when calling SandboxNetworkScenariosApi->activate_network_scenario: %s\n' % e)

    return -1
    # End of function activate_network_scenario


#### The deactivate function

The process to deactivate a scenario is based on an HTTP DELETE request with the URL '/sandboxNetworkScenarios/{sandbox_name}?network_scenario_id={network_scenario_id}'.


In [ ]:
def deactivate_network_scenario(sandbox: str) -> int:
    """
    Deactivate the current network scenario.

    :param sandbox: The MEC Sandbox instance to use
    :return: 0 on success, -1 otherwise
    """

    global MEC_SANDBOX_API_URL, logger, configuration, nw_scenarios, nw_scenario_idx

    logger.debug('>>> deactivate_network_scenario: ' + sandbox)

    try:
        nw = swagger_client.SandboxNetworkScenariosApi(sandbox_api)
        result = nw.sandbox_network_scenario_delete(sandbox, nw_scenarios[nw_scenario_idx].id, async_req = False)  # noqa: E501
        logger.debug('deactivate_network_scenario: result: ' + str(result))
        return result
    except ApiException as e:
        logger.error('Exception when calling SandboxNetworkScenariosApi->deactivate_network_scenario: %s\n' % e)

    return -1
    # End of function deactivate_network_scenario


Now, it is time to create the second iteration of our MEC application.

The sequence is the following:
- Login
- Print sandbox identifier
- Print available network scenarios
- Activate a network scenario
- Check that the network scenario is activated and the MEC services are running
- Deactivate a network scenario
- Logout
- Check that logout is effective



In [ ]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Activate a network scenario
        - Check that the network scenario is activated and the MEC services are running
        - Deactivate a network scenario
        - Logout
        - Check that logout is effective
    """ 
    global logger, nw_scenarios 

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error('Failed to instanciate a MEC Sandbox')
        return

    # Print sandbox identifier
    logger.info('Sandbox created: ' + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error('Failed to retrieve the list of network scenarios')
    elif len(nw_scenarios) != 0:
        logger.info('nw_scenarios: %s', str(type(nw_scenarios[0])))
        logger.info('nw_scenarios: %s', str(nw_scenarios))
        # Wait for the MEC Sandbox is running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running
    else:
        logger.info('nw_scenarios: No scenario available')

    # Activate a network scenario based on a list of criterias (hard coded!!!)
    if activate_network_scenario(sandbox) == -1:
        logger.error('Failed to activate network scenario')
    else:
        logger.info('Network scenario activated: ' + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Check that the network scenario is activated and the MEC services are running 
    logger.info('To check that the network scenario is activated, verify on the MEC Sandbox server that the MEC services are running (kubectl get pods -A)')
    time.sleep(30) # Sleep for 30 seconds

    # Deactivate a network scenario based on a list of criterias (hard coded!!!)
    if deactivate_network_scenario(sandbox) == -1:
        logger.error('Failed to deactivate network scenario')
    else:
        logger.info('Network scenario deactivated: ' + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are terminated
        time.sleep(STABLE_TIME_OUT)

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug('To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A)')
  
    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Fourth step: Create and delete an appliction instance id

To enable our MEC application to be part of the activated network scenario, we need to request the MEC sandbox to create a new application instance identifier. Our MEC application will use this identifier to register to the MEC Sandbox according to MEC 011.

#### The appliction instance id creation function



In [ ]:
def request_application_instance_id(sandbox: str) -> swagger_client.models.ApplicationInfo:
    """
    """

    global MEC_PLTF, logger, configuration

    logger.debug('>>> request_application_instance_id: ' + sandbox)

    # Create a instance of our MEC application
    a = swagger_client.models.ApplicationInfo(id=str(uuid.uuid4()), name='JupyterMecApp', node_name=MEC_PLTF, type='USER')  # noqa: E501
    print(a)
    
    try:
        nw = swagger_client.SandboxAppInstancesApi(sandbox_api)
        result = nw.sandbox_app_instances_post(a, sandbox, async_req = False)  # noqa: E501
        logger.debug('request_application_instance_id: result: ' + str(result))
        return result
    except ApiException as e:
        logger.error('Exception when calling SandboxAppInstancesApi->sandbox_app_instances_post: %s\n' % e)

    return None
    # End of function request_application_instance_id

#### The appliction instance id deletion function

In [ ]:
def delete_application_instance_id(sandbox: str, id: str) -> int:
    """
    """

    global logger, configuration

    logger.debug('>>> delete_application_instance_id: ' + sandbox)
    logger.debug('>>> delete_application_instance_id: ' + id)

    try:
        nw = swagger_client.SandboxAppInstancesApi(sandbox_api)
        result = nw.sandbox_app_instances_delete(sandbox, id, async_req = False)  # noqa: E501
        logger.debug('delete_application_instance_id: result: ' + str(result))
        return result
    except ApiException as e:
        logger.error('Exception when calling SandboxAppInstancesApi->sandbox_app_instances_delete: %s\n' % e)

    return -1
    # End of function deletet_application_instance_id

#### Getting the list of applications

In [ ]:
def get_applications_list(sandbox: str) -> list:
    """
    """

    global MEC_SANDBOX_API_URL, logger, configuration

    logger.debug('>>> get_applications_list: ' + sandbox)

    try:
        nw = swagger_client.SandboxAppInstancesApi(sandbox_api)
        result = nw.sandbox_app_instances_get(sandbox, async_req = False)  # noqa: E501
        logger.debug('get_applications_list: result: ' + str(result))
        return result
    except ApiException as e:
        logger.error('Exception when calling SandboxAppInstancesApi->get_applications_list: %s\n' % e)

    return None    
    # End of function delete_application_instance_id

It is time now to create the our third iteration of our MEC application.

The sequence is the following:
- Login
- Print sandbox identifier
- Print available network scenarios
- Activate a network scenario
- Request for a new application instance identifier
- Retrieve the list of the applications instance identifier
- Check the demo application is present in the list of applications
- Delete our application instance identifier
- Deactivate a network scenario
- Logout
- Check that logout is effective


In [ ]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Activate a network scenario
        - Request for a new application instance identifier
        - Retrieve the list of the applications instance identifier
        - Check the demo application is present in the list of applications
        - Deactivate a network scenario
        - Logout
        - Check that logout is effective
    """ 
    global logger, nw_scenarios

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error('Failed to instanciate a MEC Sandbox')
        return

    # Print sandbox identifier
    logger.info('Sandbox created: ' + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error('Failed to retrieve the list of network scenarios')
    elif len(nw_scenarios) != 0:
        logger.info('nw_scenarios: %s', str(type(nw_scenarios[0])))
        logger.info('nw_scenarios: %s', str(nw_scenarios))
        # Wait for the MEC Sandbox is running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running
    else:
        logger.info('nw_scenarios: No scenario available')

    # Activate a network scenario based on a list of criterias (hard coded!!!)
    if activate_network_scenario(sandbox) == -1:
        logger.error('Failed to activate network scenario')
    else:
        logger.info('Network scenario activated: ' + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Request for a new application instance identifier
    app_inst_id = request_application_instance_id(sandbox)
    if app_inst_id == None:
        logger.error('Failed to request an application instance identifier')
    else:
        logger.info('app_inst_id: %s', str(type(app_inst_id)))
        logger.info('app_inst_id: %s', str(app_inst_id))

    # Check the demo application is present in the list of applications
    app_list = get_applications_list(sandbox)
    if app_list is None:
        logger.error('Failed to request the list of applications')
    else:
        logger.info('app_list: %s', str(type(app_list)))
        logger.info('app_list: %s', str(app_list))
        # Check if our application is present in the list of applications
        found = False
        for item in app_list:
            if item.id == app_inst_id.id:
                found = True
                break
        if not found:
            logger.error('Failed to retrieve our application instance identifier')

    # Delete the application instance identifier
    if delete_application_instance_id(sandbox, app_inst_id.id) == -1:
        logger.error('Failed to delete the application instance identifier')
    else:
        logger.info('app_inst_id deleted: ' + app_inst_id.id)

    # Deactivate a network scenario based on a list of criterias (hard coded!!!)
    if deactivate_network_scenario(sandbox) == -1:
        logger.error('Failed to deactivate network scenario')
    else:
        logger.info('Network scenario deactivated: ' + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are terminated
        time.sleep(STABLE_TIME_OUT)

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug('To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A)')
  
    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()


## MEC Registration and the READY confirmation

Having an application instance identifier allows us to register with the MEC Sandbox and interact with it (e.g. to send service queries, to subscribe to events and to recieve notifications...).

The standard MEC 011 Clause 5.2.2 MEC application start-up describes the start up process. Basically, our MEC application has to:
1. Indicates that it is running by sending a Confirm Ready message
2. Retrieve the list of MEC services 

To do so, a MEC application needs to be able to send requests but also to receive notifications (POST requests) and to reply to them.

### Fifth step: Send the READY confirmation

Sending READY confirmation is described by MEC 011 Clause 5.2.2 MEC application start-up.


In [ ]:
def send_ready_confirmation(sandbox_name: str, app_inst_id: swagger_client.models.application_info.ApplicationInfo) -> int:
    global MEC_PLTF, logger

    logger.debug('>>> send_ready_confirmation: ' + app_inst_id.id)
    try:
        url = '/' + sandbox_name + '/' + MEC_PLTF + '/mec_app_support/v2/applications/' + app_inst_id.id + '/confirm_ready'
        logger.debug('send_ready_confirmation: url: ' + url)
        header_params = {}
        # HTTP header `Accept`
        header_params['Accept'] = service_api.select_header_accept(['application/json'])  # noqa: E501
        # HTTP header `Content-Type`
        header_params['Content-Type'] = service_api.select_header_accept(['application/json'])  # noqa: E501
        # JSON indication READY
        dict_body = {}
        dict_body['indication'] = 'READY'
        body = json.dumps(dict_body)
        logger.debug('send_ready_confirmation: body: ' + body)
        result = service_api.call_api(url, 'POST', header_params=header_params, body=body, async_req=False)
        return 0
    except ApiException as e:
        logger.error('Exception when calling call_api: %s\n' % e)
    return -1
    # End of function send_ready_confirmation

In addition, our MEC application is registering to AppTerminationNotificationSubscription and it needs to delete its subscription when terminating.

At this stage, it is important to note that all subscription deletion use the same format: <subscription URL>/<subscription identifier> (see ETSI MEC GS 003 [16]). 
In this case, it the AppTerminationNotificationSubscription is 'sub-1234', the URIs to do the susbscription and to delete it are:
- MEC_SANDBOX_URL + '/' + sandbox_name + '/' + MEC_PLTF + '/mec_app_support/v2/applications/' + app_inst_id + '/subscriptions'
- MEC_SANDBOX_URL + '/' + sandbox_name + '/' + MEC_PLTF + '/mec_app_support/v2/applications/' + app_inst_id + '/subscriptions/sub-1234'

So, it will be usefull to create a small function to extract the subscription identifier from either the HTTP Location header or from the Link field found into the reponse body data structure. 

#### Subscribing to application termination

In [ ]:
def send_subscribe_termination(sandbox_name: str, app_inst_id: swagger_client.models.application_info.ApplicationInfo) -> int:
    global MEC_PLTF, logger

    logger.debug('>>> send_subscribe_termination: ' + app_inst_id.id)
    try:
        url = '/' + sandbox_name + '/' + MEC_PLTF + '/mec_app_support/v2/applications/' + app_inst_id.id + '/subscriptions'
        logger.debug('send_subscribe_termination: url: ' + url)
        header_params = {}
        # HTTP header `Accept`
        header_params['Accept'] = service_api.select_header_accept(['application/json'])  # noqa: E501
        # HTTP header `Content-Type`
        header_params['Content-Type'] = service_api.select_header_accept(['application/json'])  # noqa: E501
        # Body
        dict_body = {}
        dict_body['subscriptionType'] = 'AppTerminationNotificationSubscription'
        dict_body['callbackReference'] = 'http://yanngarcia.ddns.net/mec011/v2/termination' # FIXME To be parameterized
        dict_body['appInstanceId'] = app_inst_id.id
        body = json.dumps(dict_body)
        logger.debug('send_subscribe_termination: body: ' + str(body))
        (result, status, headers) = service_api.call_api(url, 'POST', header_params=header_params, body=str(body), async_req=False)
        logger.debug('send_subscribe_termination: headers: ' + str(headers))
        return extract_sub_id(url, headers['Location'])
    except ApiException as e:
        logger.error('Exception when calling call_api: %s\n' % e)
    return None
    # End of function send_subscribe_termination

#### Extracting subscription identifier

In [ ]:
def extract_sub_id(base_url: str, resource_url: str) -> str:
    global logger

    logger.debug('>>> extract_sub_id: base_url: ' + base_url)
    logger.debug('>>> extract_sub_id: resource_url: ' + resource_url)

    e = re.compile(re.escape(base_url) + '/(?P<sub_id>.*)', re.DOTALL | re.VERBOSE)
    m = e.match(resource_url)
    if m:
        if m.groupdict() != None:
            if 'sub_id' in m.groupdict():
                return m.groupdict()['sub_id']

    return None
    # End of function extract_sub_id

#### Delete subscription to application termination

In [ ]:
def delete_subscribe_termination(sandbox_name: str, app_inst_id: swagger_client.models.application_info.ApplicationInfo, sub_id: str) -> int:
    global MEC_PLTF, logger

    logger.debug('>>> delete_subscribe_termination: ' + app_inst_id.id)
    try:
        url = '/' + sandbox_name + '/' + MEC_PLTF + '/mec_app_support/v2/applications/' + app_inst_id.id + '/subscriptions/' + sub_id
        logger.debug('delete_subscribe_termination: url: ' + url)
        header_params = {}
        # HTTP header `Accept`
        header_params['Accept'] = service_api.select_header_accept(['application/json'])  # noqa: E501
        # HTTP header `Content-Type`
        header_params['Content-Type'] = service_api.select_header_accept(['application/json'])  # noqa: E501
        service_api.call_api(url, 'DELETE', header_params=header_params, async_req=False)
        return 0
    except ApiException as e:
        logger.error('Exception when calling call_api: %s\n' % e)
    return -1
    # End of function delete_subscribe_termination

Now, it is time now to create the our fifth iteration of our MEC application.

The sequence is the following:
- Login
- Print sandbox identifier
- Print available network scenarios
- Activate a network scenario
- Request for a new application instance identifier
- Send READY confirmation
- Subscribe to AppTerminationNotificationSubscription
- Check list of services
- Delete AppTerminationNotification subscription
- Delete our application instance identifier
- Deactivate a network scenario
- Logout
- Check that logout is effective


In [ ]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Activate a network scenario
        - Request for a new application instance identifier
        - Send READY confirmation
        
        - Subscribe to AppTermination Notification
        - Send Termination
        - Delete AppTerminationNotification subscription
        - Delete our application instance identifier
        - Deactivate a network scenario
        - Logout
        - Check that logout is effective
    """ 
    global logger, nw_scenarios

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error('Failed to instanciate a MEC Sandbox')
        return

    # Print sandbox identifier
    logger.info('Sandbox created: ' + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error('Failed to retrieve the list of network scenarios')
    elif len(nw_scenarios) != 0:
        logger.info('nw_scenarios: %s', str(type(nw_scenarios[0])))
        logger.info('nw_scenarios: %s', str(nw_scenarios))
        # Wait for the MEC Sandbox is running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running
    else:
        logger.info('nw_scenarios: No scenario available')

    # Activate a network scenario based on a list of criterias (hard coded!!!)
    if activate_network_scenario(sandbox) == -1:
        logger.error('Failed to activate network scenario')
    else:
        logger.info('Network scenario activated: ' + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Request for a new application instance identifier
    app_inst_id = request_application_instance_id(sandbox)
    if app_inst_id == None:
        logger.error('Failed to request an application instance identifier')
    else:
        logger.info('app_inst_id: %s', str(app_inst_id))

    # Send READY confirmation
    logger.info('>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>')
    sub_id = None
    if send_ready_confirmation(sandbox, app_inst_id) == -1:
        logger.error('Failed to send confirm_ready')
    else:
        # Subscribe to AppTerminationNotificationSubscription
        sub_id = send_subscribe_termination(sandbox, app_inst_id)
        if sub_id == None:
            logger.error('Failed to do the subscription')
        else:
            logger.info('sub_id: %s', sub_id)

    # Any processing here
    time.sleep(STABLE_TIME_OUT)
    logger.info('***************************************************************************************')
    print('curl --verbose -X POST "https://mec-platform2.etsi.org/'+ sandbox + '/mep1/mec_app_support/v2/applications/' + app_inst_id.id + '/confirm_ready" -H"Accept: application/json" -H"Content-Type: application/json" -d"{\\"indication\\": \\"READY\\"}"')
    time.sleep(60) # Sleep for 30 seconds
    logger.info('***************************************************************************************')

    # Delete AppTerminationNotification subscription
    if sub_id is not None:
        if delete_subscribe_termination(sandbox, app_inst_id, sub_id) == -1:
            logger.error('Failed to delete the application instance identifier')
        else:
            logger.info('app_inst_id deleted: ' + app_inst_id.id)

    # Delete the application instance identifier
    if delete_application_instance_id(sandbox, app_inst_id.id) == -1:
        logger.error('Failed to delete the application instance identifier')
    else:
        logger.info('app_inst_id deleted: ' + app_inst_id.id)

    # Deactivate a network scenario based on a list of criterias (hard coded!!!)
    if deactivate_network_scenario(sandbox) == -1:
        logger.error('Failed to deactivate network scenario')
    else:
        logger.info('Network scenario deactivated: ' + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are terminated
        time.sleep(STABLE_TIME_OUT)

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug('To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A)')
  
    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Conclusion: Create two procedures for the setup and the termination of our MEC application


#### The procedure for the setup of a MEC application

This function provides the steps to setup a MEC application and to be ready to use the MEC service exposed by the created MEC Sandbox.


In [ ]:
def mec_app_setup():
    """
    This function provides the steps to setup a MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Activate a network scenario
        - Request for a new application instance identifier
        - Send READY confirmation
        - Subscribe to AppTermination Notification
    """
    global logger, nw_scenarios

    # Login
    sandbox = process_login()
    if sandbox is None:
        logger.error('Failed to instanciate a MEC Sandbox')
        return

    # Print sandbox identifier
    logger.info('Sandbox created: ' + sandbox)
    # Wait for the MEC Sandbox is running
    time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Print available network scenarios
    nw_scenarios = get_network_scenarios(sandbox)
    if nw_scenarios is None:
        logger.error('Failed to retrieve the list of network scenarios')
    elif len(nw_scenarios) != 0:
        logger.info('nw_scenarios: %s', str(type(nw_scenarios[0])))
        logger.info('nw_scenarios: %s', str(nw_scenarios))
        # Wait for the MEC Sandbox is running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running
    else:
        logger.info('nw_scenarios: No scenario available')

    # Activate a network scenario based on a list of criterias (hard coded!!!)
    if activate_network_scenario(sandbox) == -1:
        logger.error('Failed to activate network scenario')
    else:
        logger.info('Network scenario activated: ' + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are running
        time.sleep(STABLE_TIME_OUT) # Wait for k8s pods up and running

    # Request for a new application instance identifier
    app_inst_id = request_application_instance_id(sandbox)
    if app_inst_id == None:
        logger.error('Failed to request an application instance identifier')
    else:
        logger.info('app_inst_id: %s', str(type(app_inst_id)))
        logger.info('app_inst_id: %s', str(app_inst_id))

    # Send READY confirmation
    sub_id = None
    if send_ready_confirmation(sandbox, app_inst_id) == -1:
        logger.error('Failed to send confirm_ready')
    else:
        # Subscribe to AppTerminationNotificationSubscription
        sub_id = send_subscribe_termination(sandbox, app_inst_id)
        if sub_id == None:
            logger.error('Failed to do the subscription')
        else:
            logger.info('sub_id: %s', sub_id)

    # Subscribe to AppTerminationNotificationSubscription
    sub_id = send_subscribe_termination(sandbox, app_inst_id)
    if sub_id == None:
        logger.error('Failed to do the subscription')
    else:
        logger.info('sub_id: %s', sub_id)

    return (sandbox, app_inst_id, sub_id)
    # End of function mec_app_setup

#### The procedure for the termination of a MEC application

This function provides the steps to terminate a MEC application.

NOTE: All subscriptions done outside of the mec_app_setup function are not deleted.

In [ ]:
def mec_app_termination(sandbox: str, app_inst_id:swagger_client.models.ApplicationInfo, sub_id: str):
    """
    This function provides the steps to setup a MEC application:
        - Login
        - Print sandbox identifier
        - Print available network scenarios
        - Activate a network scenario
        - Request for a new application instance identifier
        - Send READY confirmation
        - Subscribe to AppTermination Notification
    """
    # Delete AppTerminationNotification subscription
    if sub_id is not None:
        if delete_subscribe_termination(sandbox, app_inst_id, sub_id) == -1:
            logger.error('Failed to delete the application instance identifier')
        else:
            logger.info('app_inst_id deleted: ' + app_inst_id.id)

    # Delete the application instance identifier
    if delete_application_instance_id(sandbox, app_inst_id.id) == -1:
        logger.error('Failed to delete the application instance identifier')
    else:
        logger.info('app_inst_id deleted: ' + app_inst_id.id)

    # Deactivate a network scenario based on a list of criterias (hard coded!!!)
    if deactivate_network_scenario(sandbox) == -1:
        logger.error('Failed to deactivate network scenario')
    else:
        logger.info('Network scenario deactivated: ' + nw_scenarios[nw_scenario_idx].id)
        # Wait for the MEC services are terminated
        time.sleep(STABLE_TIME_OUT)

    # Logout
    process_logout(sandbox)

    # Check that logout is effective
    logger.debug('To check that logout is effective, verify on the MEC Sandbox server that the MEC Sandbox is removed (kubectl get pods -A)')
  
    # End of function mec_app_termination

## Create our second MEC application: how to use MEC Services

After doing the logging, network scenario activation, MEC application instance creation steps, we are ready to exploit the MEC services exposed by the MEC Sandbox.

In this clause, we use the following functionalities provided by MEC-030:
- Getting UU unicast provisioning information (ETSI GS MEC 030 Clause 5.5.1)
- Subscribe to the V2X message distribution server (ETSI GS MEC 030 Clause 5.5.7)


### Getting UU unicast provisioning information

The purpose is to query provisioning information for V2X communication over Uu unicast.

In [ ]:
def send_uu_unicast_provisioning_info(sandbox_name: str, ecgi: str) -> int:
    global MEC_SANDBOX_URL, MEC_PLTF, logger

    try:
        url = MEC_SANDBOX_URL + '/' + sandbox_name + '/' + MEC_PLTF + '/vis/v2/queries/uu_unicast_provisioning_info?location_info=ecgi,' + ecgi
        logger.debug('send_uu_unicast_provisioning_info: url: ' + url)
        header_params = {}
        # HTTP header `Accept`
        header_params['Accept'] = service_api.select_header_accept(['application/json'])  # noqa: E501
        # HTTP header `Content-Type`
        header_params['Content-Type'] = service_api.select_header_accept(['application/json'])  # noqa: E501
        result = service_api.call_api(url, 'POST', header_params=header_params, async_req=False)
        logger.debug('send_uu_unicast_provisioning_info: result" + result)
        return result
    except ApiException as e:
        logger.error('Exception when calling call_api: %s\n' % e)
    return Node
    # End of function send_uu_unicast_provisioning_info

let's create the our second MEC application.
The sequence is the following:
- Mec application setup
- Get UU unicast provisioning information
- Mec application termination

In [ ]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Mec application setup
        - Get UU unicast provisioning information
        - Mec application termination
    """ 
    global logger, nw_scenarios

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Login
    (sandbox, app_inst_id, sub_id) = mec_app_setup()

    ecgi = "268708941961,268711972264" # List of ecgi spearated by a ','
    result = send_uu_unicast_provisioning_info(sandbox_name, ecgi)
    if result is None:
        logger.error('Failed to get UU unicast provisioning information')
    else:
        logger.info('UU unicast provisioning information: ", result)

    mec_app_termination(sandbox, app_inst_id, sub_id)

    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Subscribing to V2X message distribution server

Here, we need to come back to the MEC 030 standard to create the type V2xMsgSubscription. It involves the creation of a set of basic types described below.

Note: These new type shall be 'JSON"serializable. It means that they have to implement the following methods:
```python
to_dict()
to_str()
__repr__()
__eq__()
__ne__()
```
`
}



In [ ]:
class LinkType(object):
    swagger_types = {'href': 'str'}
    attribute_map = {'href': 'href'}
    def __init__(self, href=None):  # noqa: E501
        self._href = href
    @property
    def href(self):
        return self._href
    @href.setter
    def href(self, href):
        self._href = href
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(
                    lambda x: x.to_dict() if hasattr(x, "to_dict') else x,
                    value
                ))
            elif hasattr(value, "to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], "to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(LinkType, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, LinkType):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class Links(object):
    swagger_types = {'self': 'LinkType'}
    attribute_map = {'self': 'self'}
    def __init__(self, self_=None):  # noqa: E501
        self._self = self_
    @property
    def self_(self):
        return self._self
    @self_.setter
    def self_(self, self_):
        self._self = self_
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(
                    lambda x: x.to_dict() if hasattr(x, "to_dict') else x,
                    value
                ))
            elif hasattr(value, "to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], "to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(Links, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, Links):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class TimeStamp(object):
    swagger_types = {'seconds': 'int', 'nano_seconds': 'int'}
    attribute_map = {'seconds': 'seconds', 'nano_seconds': 'nanoSeconds'}
    def __init__(self, seconds=None, nano_seconds=None):  # noqa: E501
        self._seconds = seconds
        self._nano_seconds = nano_seconds
    @property
    def seconds(self):
        return self._seconds
    @seconds.setter
    def seconds(self, seconds):
        self._seconds = seconds
    @property
    def nano_seconds(self):
        return self._nano_seconds
    @nano_seconds.setter
    def nano_seconds(self, nano_seconds):
        self._nano_seconds = nano_seconds
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(
                    lambda x: x.to_dict() if hasattr(x, "to_dict') else x,
                    value
                ))
            elif hasattr(value, "to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], "to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(TimeStamp, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, TimeStamp):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

### Subscribing to V2X message distribution server

The cell bellow implements the V2xMsgSubscription data structure."`
}



In [ ]:
class V2xMsgSubscription(object):
    swagger_types = {'links': 'Links', 'callback_reference': 'str', 'filter_criteria': 'V2xMsgSubscriptionFilterCriteria', 'request_test_notification': 'bool', 'subscription_type': 'str'}
    attribute_map = {'links': 'Links', 'callback_reference': 'callbackReference', 'filter_criteria': 'filterCriteria', 'request_test_notification': 'requestTestNotification', 'subscription_type': 'subscriptionType'}
    def __init__(self, links=None, callback_reference=None, filter_criteria=None, request_test_notification=None):  # noqa: E501
        self._links = None
        self._callback_reference = None
        self._filter_criteria = None
        self._request_test_notification = None
        self._subscription_type = "V2xMsgSubscription"
        if links is not None:
            self.links = links
        if callback_reference is not None:
            self.callback_reference = callback_reference
        if filter_criteria is not None:
            self.filter_criteria = filter_criteria
        if request_test_notification is not None:
            self.request_test_notification = request_test_notification
    @property
    def links(self):
        return self._links
    @links.setter
    def links(self, links):
        self_.links = links
    @property
    def callback_reference(self):
        return self._callback_reference
    @callback_reference.setter
    def callback_reference(self, callback_reference):
        self._callback_reference = callback_reference
    @property
    def links(self):
        return self._links
    @links.setter
    def links(self, links):
        self._links = links
    @property
    def filter_criteria(self):
        return self._filter_criteria
    @filter_criteria.setter
    def filter_criteria(self, filter_criteria):
        self._filter_criteria = filter_criteria
    @property
    def request_test_notification(self):
        return self._request_test_notification
    @request_test_notification.setter
    def request_test_notification(self, request_test_notification):
        self._request_test_notification = request_test_notification
    @property
    def subscription_type(self):
        return self._subscription_type
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(
                    lambda x: x.to_dict() if hasattr(x, "to_dict') else x,
                    value
                ))
            elif hasattr(value, "to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], "to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(V2xMsgSubscription, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, V2xMsgSubscription):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

class V2xMsgSubscriptionFilterCriteria(object):
    swagger_types = {'msg_type': 'list[str]', 'std_organization': 'str'}
    attribute_map = {'msg_type': 'MsgType', 'std_organization': 'stdOrganization'}
    def __init__(self, msg_type, std_organization):  # noqa: E501
        self._msg_type = None
        self._std_organization = None
        self.msg_type = msg_type
        self.std_organization = std_organization
    @property
    def msg_type(self):
        return self._msg_type
    @msg_type.setter
    def msg_type(self, msg_type):
        self._msg_type = msg_type
    @property
    def std_organization(self):
        return self._std_organization
    @std_organization.setter
    def std_organization(self, std_organization):
        self._std_organization = std_organization
    def to_dict(self):
        result = {}
        for attr, _ in six.iteritems(self.swagger_types):
            value = getattr(self, attr)
            if isinstance(value, list):
                result[attr] = list(map(
                    lambda x: x.to_dict() if hasattr(x, "to_dict') else x,
                    value
                ))
            elif hasattr(value, "to_dict'):
                result[attr] = value.to_dict()
            elif isinstance(value, dict):
                result[attr] = dict(map(
                    lambda item: (item[0], item[1].to_dict())
                    if hasattr(item[1], "to_dict') else item,
                    value.items()
                ))
            else:
                result[attr] = value
        if issubclass(V2xMsgSubscriptionFilterCriteria, dict):
            for key, value in self.items():
                result[key] = value
        return result
    def to_str(self):
        return pprint.pformat(self.to_dict())
    def __repr__(self):
        return self.to_str()
    def __eq__(self, other):
        if not isinstance(other, V2xMsgSubscriptionFilterCriteria):
            return False
        return self.__dict__ == other.__dict__
    def __ne__(self, other):
        return not self == other

Here is the V2X message subscription function. The body contains a 'JSON' serialized instance of the class V2xMsgSubscription.

In [ ]:
def subscribe_v2x_message(sandbox_name: str, v2xMsgSubscription: V2xMsgSubscription) -> int:
    global MEC_SANDBOX_URL, MEC_PLTF, CALLBACK_URI, logger

    try:
        url = MEC_SANDBOX_URL + '/' + sandbox_name + '/' + MEC_PLTF + '/vis/v2/subscriptions'
        logger.debug('subscribe_v2x_message: url: ' + url)
        header_params = {}
        # HTTP header `Accept`
        header_params['Accept'] = service_api.select_header_accept(['application/json'])  # noqa: E501
        # HTTP header `Content-Type`
        header_params['Content-Type'] = service_api.select_header_accept(['application/json'])  # noqa: E501
        # Subscription body
        body = json.dumps(v2xMsgSubscription.to_dict())
        logger.debug('subscribe_v2x_message: body: ' + body)
        (result, status, headers) = sandbox_api.call_api(url, 'POST', header_params=header_params, body=body, async_req=False)
        logger.debug('subscribe_v2x_message: result: ' + result)
        logger.debug('subscribe_v2x_message: status: ' + status)
        logger.debug('subscribe_v2x_message: headers: ' + headers)
        return (result, status, headers)
    except ApiException as e:
        logger.error('Exception when calling call_api: %s\n' % e)
    return -1
    # End of function subscribe_v2x_message

Finally, here is how to implement the V2XMessage subscription:

In [ ]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Mec application setup
        - Subscribe to V2XMessage
        - Mec application termination
    """ 
    global MEC_SANDBOX_URL, MEC_PLTF, CALLBACK_URI, logger

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Login
    (sandbox, app_inst_id, sub_id) = mec_app_setup()

    filter_criteria = V2xMsgSubscriptionFilterCriteria(['1', '2'], 'ETSI')
    v2xMsgSubscription = V2xMsgSubscription(callback_reference = CALLBACK_URI + '/vis/v2/v2x_msg_notification', filter_criteria = filter_criteria)
    result = subscribe_v2x_message(sandbox, v2xMsgSubscription)
    if result is None:
        logger.error('Failed to get UU unicast provisioning information')
    else:
        logger.info('UU unicast provisioning information: ", result)

    mec_app_termination(sandbox, app_inst_id, sub_id)

    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()


### Notification support

To recieve notifcation, our MEC application is required to support an HTTP listenener to recieve POST request from the MEC Sandbox and replto repry to them: this is the notification mechanism.

The class HTTPRequestHandler (see cell below) provides the suport of such mechanism.


In [ ]:
class HTTPRequestHandler(BaseHTTPRequestHandler):

    def do_POST(self):
        if re.search(CALLBACK_URI, self.path):
            ctype, pdict = _parse_header(self.headers.get('content-type'))
            if ctype == "application/json":
                length = int(self.headers.get('content-length'))
                rfile_str = self.rfile.read(length).decode('utf8')
                data = parse.parse_qs(rfile_str, keep_blank_values=True)
                record_id = self.path.split('/')[-1]
                LocalData.records[record_id] = data
                print('addrecord %s: %s' % (record_id, data))
                self.send_response(HTTPStatus.OK)
            else:
                self.send_response(HTTPStatus.BAD_REQUEST, 'Only application/json is supported')
        else:
            self.send_response(HTTPStatus.BAD_REQUEST, 'Unsupported URI')
        self.end_headers()

    def do_GET(self):
        self.send_response(HTTPStatus.BAD_REQUEST)
        self.end_headers()
    # End of class HTTPRequestHandler

class LocalData(object):
    records = {}
    # End of class LocalData

### Put all together

let's add a subscription the our previous MEC application.
The sequence is the following:
- Mec application setup
- Get UU unicast provisioning information
- Add subscription
- Mec application termination

In [ ]:
def process_main():
    """
    This is the second sprint of our skeleton of our MEC application:
        - Mec application setup
        - Get UU unicast provisioning information
        - Add subscription
        - Mec application termination
    """ 
    global logger, nw_scenarios

    logger.debug('Starting at ' + time.strftime('%Y%m%d-%H%M%S'))
    logger.debug('\t pwd= ' + os.getcwd())

    # Login
    (sandbox, app_inst_id, sub_id) = mec_app_setup()

    ecgi = "268708941961,268711972264" # List of ecgi spearated by a ','
    result = send_uu_unicast_provisioning_info(sandbox_name, ecgi)
    if result is None:
        logger.error('Failed to get UU unicast provisioning information')
    else:
        logger.info('UU unicast provisioning information: ", result)

    # Start notification server in a daemonized thread
    notification_server = threading.Thread(name='notification_server', target=start_server, args=(LISTENER_IP, LISTENER_PORT))
    notification_server.setDaemon(True) # Set as a daemon so it will be killed once the main thread is dead.
    notification_server.start()
    # Continue
    subscribe_v2x_message()

    # Wait for notification
    time.sleep(STABLE_TIME_OUT)

    delete_subscribe_v2x_message()

    mec_app_termination(sandbox, app_inst_id, sub_id)

    logger.debug('Stopped at ' + time.strftime('%Y%m%d-%H%M%S'))
    # End of function process_main

if __name__ == '__main__':
    process_main()


# Annexes

## Annex A: How to use an existing MEC sandbox instance

This case is used when the MEC Sandbox API is not used. The procedure is the following:
- Log to the MEC Sandbox using a WEB browser
- Select a network scenario
- Create a new application instance

When it is done, the newly created application instance is used by your application when required. This application instance is usually passed to your application in the command line or using a configuration file


### Bibliography

1. ETSI GS MEC 002 (V2.2.1) (01-2022): "Multi-access Edge Computing (MEC); Phase 2: Use Cases and Requirements".
2. ETSI GS MEC 010-1 (V1.1.1) (10-2017): "Mobile Edge Computing (MEC); Mobile Edge Management; Part 1: System, host and platform management".
3. ETSI GS MEC 010-2 (V2.2.1) (02-2022): "Multi-access Edge Computing (MEC); MEC Management; Part 2: Application lifecycle, rules and requirements management".
4. ETSI GS MEC 011 (V3.1.1) (09-2022): "Multi-access Edge Computing (MEC); Edge Platform Application Enablement".
5. ETSI GS MEC 012 (V2.2.1) (02-2022): "Multi-access Edge Computing (MEC); Radio Network Information API".
6. ETSI GS MEC 013 (V2.2.1) (01-2022): "Multi-access Edge Computing (MEC); Location API".
7. ETSI GS MEC 014 (V2.1.1) (03-2021): "Multi-access Edge Computing (MEC); UE Identity API".
8. ETSI GS MEC 015 (V2.1.1) (06-2020): "Multi-Access Edge Computing (MEC); Traffic Management APIs".
9. ETSI GS MEC 016 (V2.2.1) (04-2020): "Multi-access Edge Computing (MEC); Device application interface".
10. ETSI GS MEC 021 (V2.2.1) (02-2022): "Multi-access Edge Computing (MEC); Application Mobility Service API".
11. ETSI GS MEC 028 (V2.3.1) (07-2022): "Multi-access Edge Computing (MEC); WLAN Access Information API".
12. ETSI GS MEC 029 (V2.2.1) (01-2022): "Multi-access Edge Computing (MEC); Fixed Access Information API".
13. ETSI GS MEC 030 (V3.2.1) (05-2022): "Multi-access Edge Computing (MEC); V2X Information Service API".
14. ETSI GR MEC-DEC 025 (V2.1.1) (06-2019): "Multi-access Edge Computing (MEC); MEC Testing Framework".
15. ETSI GR MEC 001 (V3.1.1) (01-2022): "Multi-access Edge Computing (MEC); Terminology".
16. ETSI GR MEC 003 (V3.1.1): Multi-access Edge Computing (MEC); 
Framework and Reference Architecture
17. [The Wiki MEC web site](https://www.etsi.org/technologies/multi-access-edge-computing)
